In [1]:
from pymongo import MongoClient

from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By

from selenium.webdriver.chrome.service import Service as ChromeService
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.chrome.service import Service
from webdriver_manager.chrome import ChromeDriverManager

from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import NoSuchElementException, TimeoutException, ElementNotInteractableException



import time

import re
from urllib.parse import urlparse

from bs4 import BeautifulSoup

from IPython.display import clear_output


In [2]:

client = MongoClient('mongodb://localhost:27017/')
db = client['Lowerated']
collection = db['RottenTomatoes']

CollectionList = list(collection.find({}))
CollectionList[:3]


[{'_id': 0,
  'url': 'https://www.rottentomatoes.com/m/shawshank_redemption',
  'audienceScore': '98%',
  'criticsScore': '89%',
  'Critic Reviews': [{'ReviewID': 1,
    'Critic': "Buffa’s Buffet\nSubscribe\nSign in\nDiscover more from Buffa’s Buffet\nBaseball and movie commentary, deep dive TV show discussion, random hockey and assorted sports takes, dad humor, and basically unfiltered access to my filthy mind.\nSubscribe\nContinue reading\nSign in\nWhy ‘Shawshank Redemption’ sits atop the rewatchable movies list\nFrank Darabont’s prison opus plays like a hit song, 30 years later.\nDAN BUFFA\nAPR 06, 2024\n2\nShare\nThere’s something unique about a great movie that also happens to be highly rewatchable. It’s not as common as a nice picture or a film that was well made yet doesn’t sit atop the pile of discs or streamer options for a revisit. Some sets are best seen once, before being broken down and discarded in your head. So if Schindler’s List is at the top of the “hard to rewatch” s

In [8]:

chrome_options = Options()
chrome_options.add_argument("--mute-audio")

service = Service('C:/Users/Muhammad Umer/.wdm/drivers/chromedriver/win64/127.0.6533.88/chromedriver-win32/chromedriver.exe')

driver = webdriver.Chrome(service=service, options=chrome_options)
driver.maximize_window()

driver.set_page_load_timeout(60)  


In [9]:

for data in CollectionList:
    
    movie_id = data['_id']
    if movie_id > 24:
        url = data['url']
        
        driver.get(url)
        time.sleep(1)
            
        driver.execute_script("window.scrollBy(0, 1000);")
        
        try:
            TotalCritics = driver.find_element(By.XPATH, '//*[@id="modules-wrap"]/div[4]/section/div[1]/rt-link')
        except NoSuchElementException:

            try:                                          
                TotalCritics = driver.find_element(By.XPATH, '//*[@id="modules-wrap"]/div[5]/section/div[1]/rt-link')
            except NoSuchElementException:

                try:                                          
                    TotalCritics = driver.find_element(By.XPATH, '//*[@id="modules-wrap"]/div[3]/section/div[1]/rt-link')
                except NoSuchElementException:

                    try:                                          
                        TotalCritics = driver.find_element(By.XPATH, '//*[@id="modules-wrap"]/div[2]/section/div[1]/rt-link')
                    except NoSuchElementException:
                        TotalCritics = None
                        
        if TotalCritics:
            Totaltxt = TotalCritics.text
            
            match = re.search(r'View All \((\d+)\)', Totaltxt)
            if match:
                num = int(match.group(1))
            else:
                num = None
                print('Number not found Regex')
            
            if num:
                parsed_url = urlparse(url)
                movie_name = parsed_url.path.split('/m/')[-1]
            
                driver.get(f'https://www.rottentomatoes.com/m/{movie_name}/reviews')
                time.sleep(1)

                print(f'{movie_name}--------------------------------- {movie_name} ---------------------------------{movie_name}')

                CurrentMovieAllReviews = []
                num -= 1
                for ReviewNum in range(1, num):
                        
                    try:
                        ReviewSite = driver.find_element(By.XPATH, f"/html/body/div[3]/main/div/div/section/div/div[1]/div[{ReviewNum}]/div[2]/p[2]/a")
                        SiteUrl = ReviewSite.get_attribute('href')
                        driver.execute_script("window.open(arguments[0], '_blank');", SiteUrl)
                        time.sleep(1)
                        
                        driver.switch_to.window(driver.window_handles[1])
                        time.sleep(1)

                        try:
                            Review = driver.find_element(By.TAG_NAME, 'body').text
                            print(Review[:10])
                            
                        except TimeoutException:
                            print(f"TimeoutException for review {ReviewNum}. Skipping.")
                            driver.close()
                            driver.switch_to.window(driver.window_handles[0])
                            continue  
                        
                        driver.close()
                        driver.switch_to.window(driver.window_handles[0])
                        
                    except (NoSuchElementException, TimeoutException):
                        
                        try:    
                            Review = driver.find_element(By.XPATH, f'//*[@id="reviews"]/div[1]/div[{ReviewNum}]/div[2]')
                            Review = Review.text
                            print(Review[:10])
                            
                        except (NoSuchElementException, ElementNotInteractableException, TimeoutException) as e:
                            Review = 'Not Found'
                            print(f"Review {ReviewNum} not found.")
                            time.sleep(60)
                            continue  
                    
                    CurrentReview ={
                        'ReviewID':	ReviewNum,
                        'Critic': Review,
                    }
                    
                    CurrentMovieAllReviews.append(CurrentReview)
                    
                    driver.execute_script("window.scrollBy(0, 150);")
                    time.sleep(1)
                    
                    if ReviewNum % 20 == 0:
                        try:
                            MoreReviews = WebDriverWait(driver, 30).until( EC.element_to_be_clickable((By.XPATH, '//*[@id="reviews"]/div[2]/rt-button')) )
                            MoreReviews.click()
                            print(f"More reviews are available and uploaded Total ReviewNum completed are: {ReviewNum}", end= " ")
                            
                        except NoSuchElementException:
                            print(f"More reviews button not found, skipping to the next Movie.")
                            break
                
                
                CurrentMovie = {
                        "_id": movie_id,
                        "Reviews": CurrentMovieAllReviews
                    }
                
                print(f'Total reviews: {ReviewNum} collected for movie: {movie_name}, so Total movies done: {movie_id}')    
                
                collection.update_one(
                    {'_id': CurrentMovie['_id']},
                    {'$set': {'Critic Reviews': CurrentMovie['Reviews']}},
                    upsert=True
                )

                
                clear_output(wait=True)

        else:
            print("Critics Reviews not found in 4 XPaths.")

# driver.quit()

1084398-life_is_beautiful--------------------------------- 1084398-life_is_beautiful ---------------------------------1084398-life_is_beautiful
Home
About
Skip to co
TimeoutException for review 3. Skipping.
Menu
Skip 
Noticias d
TimeoutException for review 6. Skipping.
Why is Chr
HOME FILM 
Skip to ma
Login
POST
HOME VIDEO
Welcome to
« Orgazmo

About Us |
EMANUEL LE
403 Forbid
Watch Film
Watch Film
This site 
Full Revie
More reviews are available and uploaded Total ReviewNum completed are: 20 Review 21 not found.
This cross
Full Revie
LIFE IS BE
Life Is Be
Watch Film
Watch Film
Review 28 not found.
Review 29 not found.
Review 30 not found.
Review 31 not found.
Review 32 not found.
Review 33 not found.
Review 34 not found.
Review 35 not found.
Review 36 not found.
Review 37 not found.
Review 38 not found.
Review 39 not found.
Review 40 not found.
Review 41 not found.
Review 42 not found.
Review 43 not found.
Review 44 not found.
Review 45 not found.
Review 46 not found.
Review 47 not fo

NoSuchWindowException: Message: no such window: target window already closed
from unknown error: web view not found
  (Session info: chrome=127.0.6533.89)
Stacktrace:
	GetHandleVerifier [0x005B8923+23283]
	(No symbol) [0x0057E934]
	(No symbol) [0x004B0733]
	(No symbol) [0x0048D2E3]
	(No symbol) [0x0051A64F]
	(No symbol) [0x0052C686]
	(No symbol) [0x005141B6]
	(No symbol) [0x004E8017]
	(No symbol) [0x004E890D]
	GetHandleVerifier [0x006AA5F3+1013699]
	GetHandleVerifier [0x006B3E4C+1052700]
	GetHandleVerifier [0x006AD4B4+1025668]
	GetHandleVerifier [0x005DEA2B+179195]
	(No symbol) [0x00586833]
	(No symbol) [0x00583198]
	(No symbol) [0x00583337]
	(No symbol) [0x0057B4BE]
	BaseThreadInitThunk [0x76E47BA9+25]
	RtlInitializeExceptionChain [0x77A1C10B+107]
	RtlClearBits [0x77A1C08F+191]


In [10]:
ReviewNum ,movie_id

(69, 25)

In [24]:
CurrentMovieAllReviews

[{'ReviewID': 1,
  'Critic': 'ONE HEAT MINUTE PRODUCTIONS\nONE HEAT MINUTE\nMIAMI NICE\nARTICLES\nTOO MANY MINUTES\nBLUS BROTHERS / IMPRINT COMPANION\nTHE DECADE PROJECT\nTOO MUCH MOVIE\nCOMPLETED PODCASTS\nABOUT\nImprint Companion is the only podcast on the Australian Internet about "DVD Culture."\nHang onto your slipcases because Alexei Toliopoulos (Finding Drago, Total Reboot) and Blake Howard (One Heat Minute) team up to unbox, unpack and unveil upcoming releases from Australia\'s boutique Blu-Ray label Imprint Films. The second episode for the November Batch features in-depth reviews of:\nFat Man and Little Boy (1989) – Imprint Collection #186\nThe Mission (1986) – Imprint Collection #185\nSchool Ties (1992) – Imprint Collection #188\nLadies and Gentlemen, the Fabulous Stains (1982) – Imprint Collection #189\nCity of God (2002) – Imprint Collection #190\nBlake Howard - Twitter & One Heat Minute Website \nAlexei Toliopoulos - Twitter & Total Reboot\nVisit imprintfilms.com.au \nPowe

In [25]:

# CurrentMovie = {
#     "_id": movie_id,
#     "Reviews": CurrentMovieAllReviews[
# }

# collection.update_one(
#     {'_id': CurrentMovie['_id']},
#     {'$set': {'Critic Reviews': CurrentMovie['Reviews']}},
#     upsert=True
# )


UpdateResult({'n': 1, 'nModified': 1, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)

Development and Testing Exception

In [119]:

driver = webdriver.Chrome()
driver.maximize_window()
driver.set_page_load_timeout(200)  


In [122]:

for data in CollectionList:
    
    movie_id = data['_id']
    if movie_id > 1:
        url = data['url']
        
        driver.get(url)
        time.sleep(1)
            
        driver.execute_script("window.scrollBy(0, 1000);")
        
        try:
            TotalCritics = driver.find_element(By.XPATH, '//*[@id="modules-wrap"]/div[4]/section/div[1]/rt-link')
        except NoSuchElementException:

            try:                                          
                TotalCritics = driver.find_element(By.XPATH, '//*[@id="modules-wrap"]/div[5]/section/div[1]/rt-link')
            except NoSuchElementException:

                try:                                          
                    TotalCritics = driver.find_element(By.XPATH, '//*[@id="modules-wrap"]/div[3]/section/div[1]/rt-link')
                except NoSuchElementException:

                    try:                                          
                        TotalCritics = driver.find_element(By.XPATH, '//*[@id="modules-wrap"]/div[2]/section/div[1]/rt-link')
                    except NoSuchElementException:
                        TotalCritics = None
                        
        if TotalCritics:
            Totaltxt = TotalCritics.text
            
            match = re.search(r'View All \((\d+)\)', Totaltxt)
            if match:
                num = int(match.group(1))
            else:
                num = None
                print('Number not found Regex')
            
            if num:
                parsed_url = urlparse(url)
                movie_name = parsed_url.path.split('/m/')[-1]
            
                driver.get(f'https://www.rottentomatoes.com/m/{movie_name}/reviews')
                time.sleep(1)



                CurrMovieAllUrls = []                
                for ReviewNum in range(1, num):
                    
                    if ReviewNum % 20 == 0:
                        print(f"Now more URLs are available and uploaded Total URLs completed: {ReviewNum}")
                        time.sleep(1)
                        
                        MoreReviews = driver.find_element(By.XPATH, '//*[@id="reviews"]/div[2]/rt-button')
                        MoreReviews.click()
                        
                        
                    try:
                        ReviewSite = driver.find_element(By.XPATH, f"/html/body/div[3]/main/div/div/section/div/div[1]/div[{ReviewNum}]/div[2]/p[2]/a")
                        SiteUrl = ReviewSite.get_attribute('href')
                        
                        CurrMovieAllUrls.append(SiteUrl)
                        time.sleep(1)
                        
                    except NoSuchElementException:
                        print(f"Review {ReviewNum} not found.")
                        CurrMovieAllUrls.append('Not Found')
                        continue
                    
                print( f' -------------------------------------- URLs completed: {ReviewNum} -------------------------------------- ' )
                        
                CurrentMovieAllReviews = []
                num -= 1
                for ReviewNum in range(0, num):
                        
                    if CurrMovieAllUrls[ReviewNum] != 'Not Found':
                        driver.execute_script("window.open(arguments[0], '_blank');", CurrMovieAllUrls[ReviewNum])
                        time.sleep(1)
                        
                        driver.switch_to.window(driver.window_handles[1])
                        
                        try:
                            Review = driver.find_element(By.TAG_NAME, 'body').text
                            print(Review[:10])
                            
                        except TimeoutException:
                            print(f"TimeoutException for review {ReviewNum}. Skipping.")
                            driver.close()
                            driver.switch_to.window(driver.window_handles[0])
                            continue  

                        driver.close()
                        driver.switch_to.window(driver.window_handles[0])
                        
                    else:
                        
                        try:
                            Review = driver.find_element(By.XPATH, f'//*[@id="reviews"]/div[1]/div[{ReviewNum}]/div[2]')
                            Review = Review.text
                            print(Review[:10])
                            
                        except NoSuchElementException:
                            Review = 'Not Found'
                            print(f"Review {ReviewNum} not found.")
                            continue  

                    
                    CurrentReview ={
                        'ReviewID':	ReviewNum,
                        'Critic': Review,
                    }
                    
                    CurrentMovieAllReviews.append(CurrentReview)
                    
                    driver.execute_script("window.scrollBy(0, 150);")
                    time.sleep(1)
                
                
                CurrentMovie = {
                        "_id": movie_id,
                        "Reviews": CurrentMovieAllReviews
                    }
                
                print(f'Total reviews: {ReviewNum} collected for movie: {movie_name}, so Total movies done: {movie_id}')    
                
                collection.update_one(
                    {'_id': CurrentMovie['_id']},
                    {'$set': {'Critic Reviews': CurrentMovie['Reviews']}},
                    upsert=True
                )


                clear_output(wait=True)

        else:
            print("Critics Reviews not found in 4 XPaths.")

# driver.quit()

Now more URLs are available and uploaded Total URLs completed: 20
Now more URLs are available and uploaded Total URLs completed: 40
Review 45 not found.
Now more URLs are available and uploaded Total URLs completed: 60
Review 61 not found.
Review 62 not found.
Review 63 not found.
Review 64 not found.
Review 65 not found.
Review 66 not found.
Review 67 not found.
Review 68 not found.
Now more URLs are available and uploaded Total URLs completed: 80
Review 81 not found.
Review 82 not found.
Review 83 not found.
Review 84 not found.
Review 85 not found.
Review 86 not found.
Review 87 not found.
Review 88 not found.
Review 89 not found.
Review 90 not found.
Review 91 not found.
Review 92 not found.
Review 93 not found.
Review 94 not found.
Review 95 not found.
Review 96 not found.
Review 97 not found.
Review 98 not found.
Review 99 not found.
Now more URLs are available and uploaded Total URLs completed: 100
Review 105 not found.
Review 112 not found.
Review 117 not found.
Now more URLs a

TimeoutException: Message: timeout: Timed out receiving message from renderer: 300.000
  (Session info: chrome=127.0.6533.74)
Stacktrace:
	GetHandleVerifier [0x00007FF7C83A9632+30946]
	(No symbol) [0x00007FF7C835E3C9]
	(No symbol) [0x00007FF7C8256FDA]
	(No symbol) [0x00007FF7C823FF7D]
	(No symbol) [0x00007FF7C823FC80]
	(No symbol) [0x00007FF7C823DE84]
	(No symbol) [0x00007FF7C823E46F]
	(No symbol) [0x00007FF7C824CC6E]
	(No symbol) [0x00007FF7C82650FF]
	(No symbol) [0x00007FF7C826AB7A]
	(No symbol) [0x00007FF7C823EBBA]
	(No symbol) [0x00007FF7C8264F4A]
	(No symbol) [0x00007FF7C82EAF1C]
	(No symbol) [0x00007FF7C82CC813]
	(No symbol) [0x00007FF7C829A6E5]
	(No symbol) [0x00007FF7C829B021]
	GetHandleVerifier [0x00007FF7C84DF83D+1301229]
	GetHandleVerifier [0x00007FF7C84EBDB7+1351783]
	GetHandleVerifier [0x00007FF7C84E2A03+1313971]
	GetHandleVerifier [0x00007FF7C83DDD06+245686]
	(No symbol) [0x00007FF7C836758F]
	(No symbol) [0x00007FF7C8363804]
	(No symbol) [0x00007FF7C8363992]
	(No symbol) 

In [126]:
from selenium.common.exceptions import TimeoutException

In [127]:
CurrentMovieAllReviews = []
num -= 1
for ReviewNum in range(0, num):
    if CurrMovieAllUrls[ReviewNum] != 'Not Found':
        try:
            driver.execute_script("window.open(arguments[0], '_blank');", CurrMovieAllUrls[ReviewNum])
            time.sleep(2)
            
            driver.switch_to.window(driver.window_handles[1])
            
            try:
                Review = driver.find_element(By.TAG_NAME, 'body').text
                print(Review[:10])
            except TimeoutException:
                print(f"TimeoutException for review {ReviewNum}. Skipping.")
                driver.close()
                driver.switch_to.window(driver.window_handles[0])
                continue  

            driver.close()
            driver.switch_to.window(driver.window_handles[0])
            
        except Exception as e:
            print(f"An error occurred. Skipping review {ReviewNum}.")
            continue  
        
    else:
        try:
            Review = driver.find_element(By.XPATH, f'//*[@id="reviews"]/div[1]/div[{ReviewNum}]/div[2]').text
            print(Review[:10])
        except NoSuchElementException:
            Review = 'Not Found'
            print(f"Review {ReviewNum} not found.")
            continue  # Skip to the next review

    CurrentReview = {
        'ReviewID': ReviewNum,
        'Critic': Review,
    }
    
    CurrentMovieAllReviews.append(CurrentReview)
    
    driver.execute_script("window.scrollBy(0, 150);")
    time.sleep(1)

CurrentMovie = {
    "_id": movie_id,
    "Reviews": CurrentMovieAllReviews
}

print(f'Total reviews: {ReviewNum} collected for movie: {movie_name}, so Total movies done: {movie_id}')    

collection.update_one(
    {'_id': CurrentMovie['_id']},
    {'$set': {'Critic Reviews': CurrentMovie['Reviews']}},
    upsert=True
)

clear_output(wait=True)

Skip to co
CRÍTICAS
E
Film
TV
Sp
Sunday, Au
BetFTW NFL
REVIEWS TH
TimeoutException for review 6. Skipping.
Facebook
T
Home
Movie
What to Wa
   STARRIN
IGN Logo
S
News Exclu
Skip to co
News Weath
Skip to ma
Skip to co
Skip to ma
Skip to co
Vanity Fai
Belief.

T
This site 
News & Fea
Search
+1-
Home
About
Internatio
This site 
New Times,
FRIDAY, AU
Explore
Se
SUBSCRIBE

Home
UK
Wo
Skip to co
This domai
Please sup
Menu
Tampa
ASIA EDITI
Skip to ma
This websi
PEOPLE
Mag
ASIA EDITI
Home
About
birmingham
Your finge
Does it ma
AskMen
SIG
Belly Fat 
This site 
Electric S
Flicks
CIN
This site 
Going Out

Home
About
Not Found

Skip to co
MAGAZINE
N
StopSmilin
This site 
Enter-To-W
Share this
Were films
The glimps
It's not j
A phenomen
Thank Warn
The Dark K
Visceral a
The Dark K
Aug 9, 200
TV
MOVIES

Skip to co
Skip to ma
This site 
NEWSLETTER
Future Mov
HOME
REVIE
The Phoeni
NOW AVAILA
This site 
"We waste 
It not onl
The Dark K
Middling a
najefektni
Heath Ledg
Despite it
The Dark K
Can one gr
Th

NameError: name 'clear_output' is not defined

In [131]:
CurrentMovieAllReviews

[{'ReviewID': 0,
  'Critic': 'Skip to content\nSearch for:\nNoticias\nReseñas\nPodcast\nEntrevistas\nConcursos\nGo to...\nNoticias\nReseñas\nPodcast\nEntrevistas\nConcursos\nSearch for:\nThrowback #61 – The Dark Knight\nPrevious Next\nView Larger Image\nThrowback #61 – The Dark Knight\nBy Fico Cangiano|2021-07-16T14:34:36-04:00July 16th, 2021|Feature, News, Podcast, Reviews|0 Comments\nShare This Story, Choose Your Platform!\nFacebookXRedditLinkedInWhatsAppTumblrPinterestVkEmail\nAbout the Author: Fico Cangiano\nRelated Posts\nReseña: TRAP\nThrowback #180 – Lost in Translation\nNuevas imágenes de SKELETON CREW\nTrailer de SPELLBOUND\nLeave A Comment\nComment\nSÍGUENOS EN\nMENU\nNoticias\nReseñas\nPodcast\nEntrevistas\nConcursos\nCONTACTOS\nPueden enviar sus mensajes a\ninfo@cinexpresspr.com\nPage load link\nGo to Top'},
 {'ReviewID': 1,
  'Critic': 'CRÍTICAS\nENTREVISTAS\nFESTIVALES\nINDUSTRIA\nCULTURA\nAGENDA\nMax\nCrítica de "Batman: el caballero de la noche": Bienvenidos al postmode

In [123]:

CurrMovieAllUrls


['https://www.escribiendocine.com/noticias/2024/03/11/140-critica-de-batman-el-caballero-de-la-noche-bienvenidos-al-postmodernismo',
 'https://akhilarora.com/christopher-nolan-movies-ranked/',
 'https://insessionfilm.com/list-christian-eulinbergs-live-action-batman-ranking/',
 'https://ftw.usatoday.com/lists/christopher-nolan-films-ranked?taid=64b930686c0e130001ec5ebd&utm_campaign=trueAnthem%3A+New+Content+%28Feed%29&utm_medium=trueAnthem&utm_source=twitter',
 'https://deepfocusreview.com/definitives/the-dark-knight/',
 'https://cinexpresspr.com/site/2021/07/16/throwback-61-the-dark-knight/',
 'http://www.richardcrouse.ca/the-dark-knight-4-%c2%bd-stars/',
 'http://gonewiththetwins.com/new/dark-knight-2008/',
 'https://www.whatsontv.co.uk/movie-talk/dark-knight-review-327567/',
 'https://theindependentcritic.com/the_dark_knight',
 'https://www.ign.com/articles/christopher-nolan-the-dark-knight-war-on-terror',
 'https://www.comicbookmovie.com/batman/the-dark-knight-review-one-of-the-grea

In [ ]:
print(ReviewNum)
Review 

138


"Your connection is not private\nAttackers might be trying to steal your information from reviews.imdb.com (for example, passwords, messages, or credit cards). Learn more\nNET::ERR_CERT_COMMON_NAME_INVALID\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\nTurn on enhanced protection to get Chrome's highest level of security\nReload\nAdvanced"